In [1]:
import pandas as pd 
import numpy as np 
import os 
import sys
import re
from pandas.testing import assert_frame_equal

from pathlib import Path

In [2]:
# TODO: run also on peptides before grouping.. and get sparsity of the dataframes



# read preprocessed_pp2 file
results_folder = Path("/media/kusterlab/internal_projects/active/TOPAS/WP31/Playground/Retrospective_study/2025.08.11_CJ_paper_cohort_replicates_celllines")

df = pd.read_csv(results_folder / "preprocessed_fp2.csv", index_col=0)
# df = pd.read_csv(results_folder / "evidence.txt", sep='\t')

# df = df.set_index(['Modified sequence', 'Gene names'])

/tmp/ipykernel_728187/1176021294.py:8: DtypeWarning: Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(results_folder / "preprocessed_fp2.csv", index_col=0)


In [3]:
df.head()

Majority protein IDs Peptide counts (unique)  Best peptide  \
Protein IDs                                                              
F2                            F2                     123           NaN   
LIMA1                      LIMA1                     585           NaN   
NCKAP1                    NCKAP1                     146           NaN   
FEN1                        FEN1                     111           NaN   
RALY                        RALY                     167           NaN   

             Number of proteins   Q-value  Score Protein names Gene names  \
Protein IDs                                                                 
F2                            1  0.000081   45.0            F2         F2   
LIMA1                         1  0.000081   45.0         LIMA1      LIMA1   
NCKAP1                        1  0.000081   45.0        NCKAP1     NCKAP1   
FEN1                          1  0.000081   45.0          FEN1       FEN1   
RALY                          1  0.000081   45.0          RALY       RALY   

                                                 Fasta headers  \
Protein IDs                                                      
F2           tr|E9PIT3|E9PIT3_HUMAN Activation peptide frag...   
LIMA1        tr|F8VRN8|F8VRN8_HUMAN LIM domain and actin-bi...   
NCKAP1       sp|Q9Y2A7|NCKP1_HUMAN Nck-associated protein 1...   
FEN1         tr|I3L3E9|I3L3E9_HUMAN Flap endonuclease 1 (Fr...   
RALY         tr|Q5QPM2|Q5QPM2_HUMAN RNA-binding protein Ral...   

             Combined Total Peptides  ...  \
Protein IDs                           ...   
F2                                75  ...   
LIMA1                            101  ...   
NCKAP1                            93  ...   
FEN1                              50  ...   
RALY                              42  ...   

             Identification metadata 9 Workflow_Test_BatchCL32  \
Protein IDs                                                      
F2                                            num_peptides=11;   
LIMA1                                         num_peptides=50;   
NCKAP1                                        num_peptides=45;   
FEN1                                          num_peptides=22;   
RALY                                          num_peptides=25;   

             Identification metadata 9 Workflow_Test_BatchCL33  \
Protein IDs                                                      
F2                                            num_peptides=11;   
LIMA1                                         num_peptides=58;   
NCKAP1                                        num_peptides=37;   
FEN1                                          num_peptides=21;   
RALY                                          num_peptides=23;   

             Identification metadata 9 Workflow_Test_BatchCL36  \
Protein IDs                                                      
F2                                             num_peptides=8;   
LIMA1                                         num_peptides=39;   
NCKAP1                                        num_peptides=40;   
FEN1                                          num_peptides=21;   
RALY                                          num_peptides=23;   

             Identification metadata 9 Workflow_Test_BatchCL37  \
Protein IDs                                                      
F2                                             num_peptides=8;   
LIMA1                                         num_peptides=50;   
NCKAP1                                        num_peptides=41;   
FEN1                                          num_peptides=23;   
RALY                                          num_peptides=22;   

             Identification metadata 9 Workflow_Test_BatchCL5  \
Protein IDs                                                     
F2                                            num_peptides=5;   
LIMA1                                        num_peptides=43;   
NCKAP1                                       num_peptides=42; 

In [ ]:
# # make a function for this format


# # # Example dataframe (already log10-transformed)
# # df = pd.DataFrame({
# #     "Gene names": ["P1", "P2", "P3", "P1", "P2", "P3"],
# #     "Batch": ["Batch1", "Batch1", "Batch1", "Batch2", "Batch2", "Batch2"],
# #     "Reporter intensity corrected 1": [5, 8, 4, 5, np.nan, 12],   # max for row 1
# #     "Reporter intensity corrected 2": [1.5, -2.0, 0.5, 8, np.nan, 11],  # should be NaN for P2
# #     "Reporter intensity corrected 3": [5.0, 5.0, 2.9, 4, np.nan, 10],    # close to max
# # })

# df_new = df.copy()

# def filter_high_dr_evidence(evidence_df, ratio_threshold: float = 0.01):
#     """
#     Filter out evidence with a log ratio below the specified threshold.
    
#     Parameters:
#     df (DataFrame): The input DataFrame containing evidence data.
#     logratio (int): The log ratio threshold for filtering.
    
#     Returns:
#     DataFrame: Filtered DataFrame with high DR evidence.
#     """
#     pat_cols = [col for col in evidence_df.columns if col.startswith('Reporter intensity corrected')]

#     # compute row-wise max
#     row_max = evidence_df[pat_cols].max(axis=1)

#     # compute ratio
#     ratio_df = evidence_df[pat_cols].div(row_max, axis=0)

#     # mask values smaller than threshold (1/100)
#     small_mask = ratio_df < 0.01

#     df_new[pat_cols] = evidence_df[pat_cols].mask(small_mask)
    
#     return df_new

# evidence_filtered = filter_high_dr_evidence(df_new)
# evidence_filtered.head()


# # expected_df = pd.DataFrame({
# #     "Gene names": ["P1", "P2", "P3", "P1", "P2", "P3"],
# #     "Batch": ["Batch1", "Batch1", "Batch1", "Batch2", "Batch2", "Batch2"],
# #     "Reporter intensity corrected 1": [5.0, 8.0, 4.0, np.nan, np.nan, 12.0],
# #     "Reporter intensity corrected 2": [np.nan, np.nan, np.nan, 8.0, np.nan, 11.0],
# #     "Reporter intensity corrected 3": [5.0, np.nan, 2.9, np.nan, np.nan, 10.0],
# # })

# # # check equality
# # assert_frame_equal(evidence_filtered, expected_df, check_dtype=False)
# # print("✅ DataFrames are equal")


Modified sequence  \
0                                _AAAHHYGAQCDKPNK_   
1                           _AAALAAAVAQDPAASGAPSS_   
2                                  _AAALCNACELSGK_   
3  _(Acetyl (Protein N-term))AAASVTPPGSLELLQPGFSK_   
4                                        _AAATPAK_   

                                            Proteins Leading proteins  \
0                                             P51970           P51970   
1                                             Q8TAE8           Q8TAE8   
2                           Q7Z392;Q7Z392-3;Q7Z392-4           Q7Z392   
3  B1AMX7;B1AMX8;B1AMY1;Q12933;Q12933-2;Q12933-3;...         Q12933-3   
4                 C9J1H7;C9JLB1;C9JWL1;C9JYW2;P19338           P19338   

   Gene names                          Raw file  Fraction           Batch  \
0      NDUFA8  4186_A01_047059_S00_U01_TMT11_R1         1  Sarcoma_Batch1   
1  GADD45GIP1  4186_A01_047059_S00_U01_TMT11_R1         1  Sarcoma_Batch1   
2    TRAPPC11  4186_A01_047059_S00_U01_TMT11_R1         1  Sarcoma_Batch1   
3       TRAF2  4186_A01_047059_S00_U01_TMT11_R1         1  Sarcoma_Batch1   
4         NCL  4186_A01_047059_S00_U01_TMT11_R1         1  Sarcoma_Batch1   

   Charge           PEP   id  ...  Reporter intensity corrected 2  \
0       5  4.126800e-02  NaN  ...                       3128910.0   
1       2  9.158400e-07  1.0  ...                       8492480.0   
2       2  1.516600e-02  2.0  ...                       3082380.0   
3       2  9.730500e-04  3.0  ...                       3915610.0   
4       2  4.122700e-02  4.0  ...                     151771000.0   

   Reporter intensity corrected 3  Reporter intensity corrected 4  \
0                       6344980.0                       8540570.0   
1                       5506730.0                       6949780.0   
2                      10329800.0                       7682140.0   
3                        793053.0                        753177.0   
4                      51842800.0                      63676400.0   

   Reporter intensity corrected 5  Reporter intensity corrected 6  \
0                       2282870.0                       6345260.0   
1                       5356810.0                       5464990.0   
2                       3590850.0                       3390220.0   
3                       4228850.0                       4007630.0   
4                      67259800.0                      87927900.0   

   Reporter intensity corrected 7  Reporter intensity corrected 8  \
0                       1447570.0                       2457050.0   
1                       4348270.0                       4341920.0   
2                       5072460.0                       5252040.0   
3                        548422.0                       2629560.0   
4                     133426000.0                      12592800.0   

   Reporter intensity corrected 9  Reporter intensity corrected 10  \
0                       1531480.0                         848382.0   
1                       8821510.0                       10336200.0   
2                       4583570.0                        3772530.0   
3                       3018180.0                        4494980.0   
4                     117798000.0                        2982860.0   

   Reporter intensity corrected 11  
0                         509407.0  
1                        8608640.0  
2                        3362060.0  
3                        4315380.0  
4                        9956810.0  

[5 rows x 22 columns]

In [ ]:
# calculate percentage of removal from df
# df_new[pat_cols].size
# diff_count = na_count_new - na_count_original
# percentage_removed = (diff_count / df_new[pat_cols].size) * 100
# percentage_removed

np.float64(2.3920892146495025)

In [ ]:
# # compare sparsity before and after 
# df_new = evidence_filtered.copy()
# df_new.to_csv(results_folder / "evidence_filtered.txt", sep='\t', index=False)

# pat_cols = [col for col in df.columns if col.startswith("Reporter")]

# # check sparsity between the two dataframes
# sparsity_original = df[pat_cols].isna().mean().mean()
# sparsity_new = df_new[pat_cols].isna().mean().mean()
# print(f"Sparsity of original dataframe: {sparsity_original:.2%}")
# print(f"Sparsity of new dataframe: {sparsity_new:.2%}")

# # count all na in both dataframes
# na_count_original = df[pat_cols].isna().sum().sum()
# na_count_new = df_new[pat_cols].isna().sum().sum()
# print(f"Number of NaN values in original dataframe: {na_count_original}")
# print(f"Number of NaN values in new dataframe: {na_count_new}")

# # calculate percentage of NaN values before and after
# percentage_na_original = (na_count_original / df[pat_cols].size) * 100
# percentage_na_new = (na_count_new / df_new[pat_cols].size) * 100
# print(f"Percentage of NaN values in original dataframe: {percentage_na_original:.2f}%")
# print(f"Percentage of NaN values in new dataframe: {percentage_na_new:.2f}%")


Sparsity of original dataframe: 8.60%
Sparsity of new dataframe: 10.99%
Number of NaN values in original dataframe: 38120509
Number of NaN values in new dataframe: 48722807
Percentage of NaN values in original dataframe: 8.60%
Percentage of NaN values in new dataframe: 10.99%


In [ ]:
# does it make more sense to just make a long format df? or a style of groupby which we already do where we also add metadata information

df_new = df.copy()

batches = {col: col.split("_")[1] for col in df.columns if "Batch" in col and "Unique" not in col}
batches

# turn around a dict to get all keys of a value
batches_reversed = {}
for key, value in batches.items():
    if value not in batches_reversed:
        batches_reversed[value] = []
    batches_reversed[value].append(key)
batches_reversed

# OBS now we do it including failed/filtered out samples

# def add_imputation_status(z):
    # return np.where(z.isna() & imputation_values.notna(), "imputed;", "")

# cols of Unique Reporter intensity is also in there


# loop over each key in batches_reversed and subset the dataframe
for batch, cols in batches_reversed.items():
    # print(batch, cols)
    pat_cols = [c for c in cols if "Reporter" in c]
    metadata_cols = [c for c in cols if "Identification" in c]

    diff_df = df[pat_cols].sub(df[pat_cols].max(axis=1), axis=0)
    small_mask = diff_df < -2  # (log10 scale: -2 means 1/100)
    df_new[pat_cols] = df[pat_cols].mask(small_mask)

    # Map reporter → metadata by matching last two parts of the column name
    for pat_col in pat_cols:
        pat_id = " ".join(pat_col.split()[-2:])  # e.g., '4 Sarcoma_Batch3'
        # print(pat_id)
        match = re.search(r'(\d+)\s+(\w+_Batch\d+)', pat_col)
        if not match:
            continue
        reporter_num, batch_id = match.groups()

        # Match exactly on reporter number + batch
        matching_meta_cols = [
            m for m in metadata_cols
            if re.search(rf'\b{reporter_num}\b.*{batch_id}$', m)
        ]

        for meta_col in matching_meta_cols:
            # Where small_mask is True, append the flag; otherwise keep existing content
            existing = df_new[meta_col].fillna("")
            df_new[meta_col] = np.where(
                small_mask[pat_col],
                existing + "high_dr_filter;",  # append
                existing  # leave as is
            )
    

In [15]:
df_new = df_new.reset_index().set_index(['Gene names'])
# keep only columns starting with 'Reporter' or 'Identification'
df_new = df_new[[col for col in df_new.columns if col.startswith(('Reporter', 'Identification'))]]
df_new.head()

Reporter intensity corrected 1 Sarcoma_Batch1  \
Gene names                                                  
SYMPK                                             8.18092   
NUP160                                            8.31544   
FARP1                                             8.38496   
UPF1                                              8.95921   
IGBP1                                             8.12729   

            Reporter intensity corrected 1 Sarcoma_Batch10  \
Gene names                                                   
SYMPK                                              8.53814   
NUP160                                             8.62241   
FARP1                                              8.59844   
UPF1                                               9.11979   
IGBP1                                              8.01138   

            Reporter intensity corrected 1 Sarcoma_Batch100  \
Gene names                                                    
SYMPK                                               8.35581   
NUP160                                              8.57695   
FARP1                                               8.38750   
UPF1                                                9.15361   
IGBP1                                               8.27681   

            Reporter intensity corrected 1 Sarcoma_Batch101  \
Gene names                                                    
SYMPK                                               8.57470   
NUP160                                              8.65006   
FARP1                                               8.24278   
UPF1                                                9.05621   
IGBP1                                               8.29214   

            Reporter intensity corrected 1 Sarcoma_Batch102  \
Gene names                                                    
SYMPK                                               8.41786   
NUP160                                              8.52986   
FARP1                                               8.27337   
UPF1                                                8.92442   
IGBP1                                               8.06430   

            Reporter intensity corrected 1 Sarcoma_Batch103  \
Gene names                                                    
SYMPK                                               8.48210   
NUP160                                              8.58101   
FARP1                                               8.82780   
UPF1                                                9.13216   
IGBP1                                               7.66873   

            Reporter intensity corrected 1 Sarcoma_Batch105  \
Gene names                                                    
SYMPK                                               8.47257   
NUP160                                              8.48085   
FARP1                                               8.75843   
UPF1                                                9.16060   
IGBP1                                               8.15377   

            Reporter intensity corrected 1 Sarcoma_Batch106  \
Gene names                                                    
SYMPK                                               8.62221   
NUP160                                              8.75529   
FARP1                                               8.26220   
UPF1                                                9.15447   
IGBP1                                               8.32110   

            Reporter intensity corrected 1 Sarcoma_Batch107  \
Gene names                                                    
SYMPK                                               8.60000   
NUP160                                              8.81129   
FARP1                                               8.71316   
UPF1                                                9.24528   
IGBP1                                               8.00358   

            Reporter intensity corrected 1 Sarcoma_Batc

In [17]:
# save as preprocessed_pp2_filtered.csv
df_new.to_csv("/media/kusterlab/internal_projects/active/TOPAS/WP31/Playground/Retrospective_study/2025.08.14_CJ_paper_cohort_robust_zscore_and_dr_filter/filter_at_protein_level/preprocessed_fp2_filtered.csv")

In [31]:
pat_cols = [col for col in df.columns if col.startswith("Reporter")]
metadata_cols = [col for col in df.columns if "Metadata" in col]

# check sparsity between the two dataframes
sparsity_original = df[pat_cols].isna().mean().mean()
sparsity_new = df_new[pat_cols].isna().mean().mean()
print(f"Sparsity of original dataframe: {sparsity_original:.2%}")
print(f"Sparsity of new dataframe: {sparsity_new:.2%}")

# count all na in both dataframes
na_count_original = df[pat_cols].isna().sum().sum()
na_count_new = df_new[pat_cols].isna().sum().sum()
print(f"Number of NaN values in original dataframe: {na_count_original}")
print(f"Number of NaN values in new dataframe: {na_count_new}")

# calculate percentage of NaN values before and after
percentage_na_original = (na_count_original / df[pat_cols].size) * 100
percentage_na_new = (na_count_new / df_new[pat_cols].size) * 100
print(f"Percentage of NaN values in original dataframe: {percentage_na_original:.2f}%")
print(f"Percentage of NaN values in new dataframe: {percentage_na_new:.2f}%")

# calculate percentage of removal from df
diff_count = na_count_new - na_count_original
percentage_removed = (diff_count / df_new[pat_cols].size) * 100
print(f"Percentage of values removed: {percentage_removed:.2f}%")

Sparsity of original dataframe: 36.69%
Sparsity of new dataframe: 62.88%
Number of NaN values in original dataframe: 15507439
Number of NaN values in new dataframe: 26576825
Percentage of NaN values in original dataframe: 36.69%
Percentage of NaN values in new dataframe: 62.88%
Percentage of values removed: 26.19%
